
### Entrada
- x1: Local da Coleta em km
- x2: Nivel da Mare em m
- x3: Umidade do Ar (%)
- x4: Índice Pluvimétrico (mm)¹
- x5: Temperatura (°C)

### Saida
- y1: pH
- y2: Condutividade Elétrica (mS.cmˉ¹)
- y3: Oxigênio Dissolvido (mg.Lˉ¹)
- y4: Sólidos Totais Dissolvidos (ppm)


In [1]:
!pip install --upgrade pip
!pip install tensorflow 
!pip install openpyxl

In [2]:
import os

os.chdir("./content")

lm_dir = "tf-levenberg-marquardt"
if not os.path.exists(lm_dir):
  !git clone https://github.com/fabiodimarco/$lm_dir

os.chdir(lm_dir)

Cloning into 'tf-levenberg-marquardt'...
remote: Enumerating objects: 53, done.
remote: Counting objects: 100% (53/53), done.
remote: Compressing objects: 100% (38/38), done.
remote: Total 53 (delta 31), reused 29 (delta 14), pack-reused 0
Receiving objects: 100% (53/53), 32.99 KiB | 16.50 MiB/s, done.
Resolving deltas: 100% (31/31), done.


In [3]:
import numpy as np
import pandas as pd

def create_dataframe(output, label):
    df = pd.read_excel("../../../data.xlsx")
    x1, x2, x3, x4, x5  = df['x1'], df['x2'], df['x3'], df['x4'], df['x5']

    input = np.vstack([x1, x2, x3, x4, x5 ]).T
    output = np.array(df[output])
    return output, input

output, input = create_dataframe(output="y3", label="oxigenio")

/tmp/ipykernel_549789/160627683.py:2: DeprecationWarning: 
Pyarrow will become a required dependency of pandas in the next major release of pandas (pandas 3.0),
(to allow more performant data types, such as the Arrow string type, and better interoperability with other libraries)
but was not found to be installed on your system.
If this would cause problems for you,
please provide us feedback at https://github.com/pandas-dev/pandas/issues/54466
        
  import pandas as pd


In [4]:
import tensorflow as tf
import numpy as np
from keras import regularizers
from keras import initializers
import levenberg_marquardt as lm

# layers, neurons
class ShuffleArchitecture:
    def __init__(self, input_size, hidden_sizes, output_size, act_h, act_o, param_reg):
        self.input_size = input_size
        self.hidden_sizes = hidden_sizes
        self.output_size = output_size
        self.act_h = act_h
        self.act_o = act_o
        self.regularizer = regularizers.L2(param_reg)
        self.initializer = initializers.RandomUniform(minval=-0.5, maxval=0.5, seed=np.random.randint(1, 10000))

    def set_architecture(self):
        self.model = tf.keras.Sequential()
        self.model.add(tf.keras.layers.Dense(self.hidden_sizes[0],
                        input_shape=(self.input_size,),
                        activation=self.act_h,
                        kernel_regularizer=self.regularizer,
                        kernel_initializer=self.initializer,                        
                        ))  # input layer
        
        for size in self.hidden_sizes[1:]:  # hidden layers
            self.model.add(tf.keras.layers.Dense(size,
                            activation=self.act_h,
                            kernel_regularizer=self.regularizer,
                            kernel_initializer=self.initializer,  
                        ))

        self.model.add(tf.keras.layers.Dense(self.output_size,
                        activation=self.act_o,
                        kernel_regularizer=self.regularizer,
                        kernel_initializer=self.initializer,  
                        ))  # output layer

    def create_model(self, _learning_rate):
        self.model.compile(
            optimizer=tf.keras.optimizers.Adam(learning_rate=_learning_rate),
            loss=tf.keras.losses.MeanSquaredError())

        self.lm_model = lm.ModelWrapper(
            tf.keras.models.clone_model(self.model))

        self.lm_model.compile(
            optimizer=tf.keras.optimizers.SGD(learning_rate=_learning_rate),
            loss=lm.MeanSquaredError())
        return(self.lm_model)

2024-03-24 18:26:30.533040: I external/local_tsl/tsl/cuda/cudart_stub.cc:31] Could not find cuda drivers on your machine, GPU will not be used.
2024-03-24 18:26:30.630661: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2024-03-24 18:26:30.630710: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2024-03-24 18:26:30.632147: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2024-03-24 18:26:30.640761: I external/local_tsl/tsl/cuda/cudart_stub.cc:31] Could not find cuda drivers on your machine, GPU will not be used.
2024-03-24 18:26:30.641381: I tensorflow/core/platform/cpu_feature_guard.cc:1

2024-03-24 18:26:33.002654: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT


In [5]:
import tensorflow as tf
import matplotlib.pyplot as plt
import time
from sklearn.model_selection import train_test_split
from keras.callbacks import EarlyStopping
from sklearn.metrics import r2_score, mean_squared_error


class TrainWithSmallDataset:
    def __init__(self, batch_size=1000):
        self.batch_size = batch_size
        self.betters = []
    
    def create_dataset(self, input, output):
      input = tf.expand_dims(tf.cast(input, tf.float32), axis=-1)
      output = tf.expand_dims(tf.cast(output, tf.float32), axis=-1)

      dataset = tf.data.Dataset.from_tensor_slices((input, output))
      dataset = dataset.shuffle(len(input))
      dataset = dataset.batch(self.batch_size).cache()
      dataset = dataset.prefetch(tf.data.experimental.AUTOTUNE)
      return (dataset, input, output)

    def split_dataset(self, input, output):
      input_train, input_vt, output_train, output_vt = train_test_split(input, output, test_size=0.3, shuffle = True)
      input_val, input_test, output_val, output_test = train_test_split(input_vt, output_vt, test_size=0.5, shuffle = True)

      self.train_dataset, self.train_input, self.train_output = self.create_dataset(input_train, output_train)
      self.val_dataset, self.val_input, self.val_output = self.create_dataset(input_val, output_val)
      self.test_dataset, self.test_input, self.test_output = self.create_dataset(input_test, output_test)
      self.vt_dataset, self.vt_input, self.vt_output = self.create_dataset(input_vt, output_vt)
      self.dataset, self.input, self.output = self.create_dataset(input, output)

      self._train = (input_train, output_train)
      self._vt = (input_vt, output_vt)
      self._val = (input_val, output_val)
      self._test = (input_test, output_test)
 
 
    
    def train_using_lm(self, train_dataset, epochs=1000):
      early_stopping_monitor = EarlyStopping(monitor='val_loss',
                                              patience=6,
                                              restore_best_weights=True)

      t2_start = time.perf_counter()
      self.results = self.lm_model.fit(train_dataset,
                                            epochs=epochs,
                                            validation_data=self.val_dataset,
                                            callbacks=[early_stopping_monitor],
                                            verbose=0)
      t2_stop = time.perf_counter()
      print("Elapsed time: ", t2_stop - t2_start)
      print ("Stopped at epoch: ", early_stopping_monitor.stopped_epoch)

    def get_metrics(self):
          self.test_prediction = self.lm_model.predict(self.test_input)

          pred = self.lm_model.predict(self.input).flatten()
          test_pred = self.test_prediction.flatten()
          val_pred = self.lm_model.predict(self.val_input).flatten()
          vt_pred = self.lm_model.predict(self.vt_input).flatten()

          r2 = r2_score(self.output, pred)
          r2_test = r2_score(self.test_output, test_pred)
          r2_val = r2_score(self.val_output, val_pred)
          r2_vt = r2_score(self.vt_output, vt_pred)

          mse = mean_squared_error(self.output, pred)
          mse_test = mean_squared_error(self.test_output, test_pred)
          mse_val = mean_squared_error(self.val_output, val_pred)
          mse_vt = mean_squared_error(self.vt_output, vt_pred)

          metrics = {
                          'r2': r2,
                          'r2_test': r2_test,
                          'r2_val': r2_val,
                          'r2_vt': r2_vt,
                          'mse': mse,
                          'mse_test': mse_test,
                          'mse_val': mse_val,
                          'mse_vt': mse_vt
                          }

          return metrics

In [6]:
from itertools import product
import pickle

class Tester:
  def __init__(self, input, output, run_times=500, dataset_run_times=10):
    self.run_times = run_times
    self.better_metrics = {}
    self.dataset_run_times = dataset_run_times
    self.input, self.output = input, output
  
  def setArchitecure(self, trainer, _hidden_sizes, _pg, _lr):
    shuffler = ShuffleArchitecture(input_size=5,
                                    hidden_sizes=_hidden_sizes,
                                    output_size=1,
                                    act_h='tanh',
                                    act_o='linear',
                                    param_reg=_pg)
    shuffler.set_architecture()    
    trainer.lm_model = shuffler.create_model(_lr)

  def Train(self, trainer, epochs=1000):
    trainer.train_using_lm(trainer.train_dataset, epochs=epochs)
    return(trainer.get_metrics(), trainer.lm_model)

  def SaveModelWeights(self, model, fileName):
    path = f"../models/{fileName}.keras"
    open(path,'w').close()
    model.save_weights(path) 

  def SaveDataset(self, trainer, fileName):
    path = f"../dataset/{fileName}.pkl" 
    with open(path, 'wb') as f:
      pickle.dump((trainer._train, trainer._vt, trainer._val, trainer._test), f)


  def LoopWeights(self, sort_by, boundarie, trainer, idx):
    better_model = 0
    save = False

    for i in range(self.run_times):
      print (f"+++++++++++ [{idx}] | {i + 1} ++++++++++++++++++")
      metrics, model = self.Train(trainer)
      if (metrics[sort_by] >= boundarie): # should be <= to descending metrics
        fileName = f"model_{idx}_{better_model}"
        self.SaveModelWeights(model, fileName)
        self.better_metrics[fileName] = metrics
        better_model += 1
        save = True
    
    return(save)

# Init
  def Loop(self, sort_by, boundarie, hidden_sizes, regularizers, learning_rate):
    trainer = TrainWithSmallDataset()

    for count, (hidden_size, reg, lr) in enumerate(product(hidden_sizes, regularizers, learning_rate), start=1):
      header =  f"Hidden Size={hidden_size}, regularizer={reg}, learning_rate={lr}"
      print(f"Testando combinacao{count}: {header}")
      self.setArchitecure(trainer, hidden_size, reg, lr)
      for j in range(self.dataset_run_times):
        trainer.split_dataset(self.input, self.output)
        if (self.LoopWeights(sort_by, boundarie, trainer, f"{count}_{j}") == True):
          self.SaveDataset(trainer, f"dataset_{count}_{j}")
          self.DisplayBetterResults(sort_by, header, f"{count}_{j}")
        self.better_metrics = {}

  def DisplayBetterResults(self, sort_by, header, dataset=0):
    df = pd.DataFrame.from_dict(self.better_metrics, orient='index')
    df = df.sort_values([sort_by])
    display(df)
    path = f'../results/metrics_{dataset}'
    df.to_excel(f"{path}.xlsx", index=True)
    print(f"DataFrame salvo em {path}")
    with open(f"{path}.txt", 'w') as arquivo:
      arquivo.write(header)

In [7]:
tester = Tester(input, output, run_times=25, dataset_run_times=10)

In [8]:
tester.Loop(sort_by='r2',
            boundarie=0.7,
            hidden_sizes = [[15],[30] , [35], [40], [55], [60], [70]],
            regularizers=[0.02, 0.1],
            learning_rate=[0.02, 0.1])

Testando combinacao1: Hidden Size=[15], regularizer=0.02, learning_rate=0.02


+++++++++++ [1_0] | 1 ++++++++++++++++++
Elapsed time:  1.4779947909992188
Stopped at epoch:  10
1/1 [==============================] - 0s 30ms/step
+++++++++++ [1_0] | 2 ++++++++++++++++++
Elapsed time:  0.48513483999977325
Stopped at epoch:  9
1/1 [==============================] - 0s 14ms/step
+++++++++++ [1_0] | 3 ++++++++++++++++++
Elapsed time:  0.3727555529994788
Stopped at epoch:  6
1/1 [==============================] - 0s 20ms/step
+++++++++++ [1_0] | 4 ++++++++++++++++++
Elapsed time:  0.4626982889994906
Stopped at epoch:  6
1/1 [==============================] - 0s 18ms/step
+++++++++++ [1_0] | 5 ++++++++++++++++++
Elapsed time:  0.45081992799987347
Stopped at epoch:  7
1/1 [==============================] - 0s 23ms/step
+++++++++++ [1_0] | 6 ++++++++++++++++++
Elapsed time:  0.4055863600005978
Stopped at epoch:  6
1/1 [==============================] - 0s 18ms/step
+++++++++++ [1_0] | 7 ++++++++++++++++++
Elapsed time:  0.3442642580002939
Stopped at epoch:  6
1/1 [========

2024-03-24 18:27:45.658920: W tensorflow/core/data/root_dataset.cc:342] Optimization loop failed: CANCELLED: Operation was cancelled


1/1 [==============================] - 0s 16ms/step
+++++++++++ [1_5] | 6 ++++++++++++++++++
Elapsed time:  0.03755384599935496
Stopped at epoch:  0
1/1 [==============================] - 0s 15ms/step
+++++++++++ [1_5] | 7 ++++++++++++++++++
Elapsed time:  0.02682922699932533
Stopped at epoch:  0
1/1 [==============================] - 0s 27ms/step
+++++++++++ [1_5] | 8 ++++++++++++++++++
Elapsed time:  0.05768494899984944
Stopped at epoch:  0
1/1 [==============================] - 0s 20ms/step
+++++++++++ [1_5] | 9 ++++++++++++++++++
Elapsed time:  0.03700193599979684
Stopped at epoch:  0
1/1 [==============================] - 0s 14ms/step
+++++++++++ [1_5] | 10 ++++++++++++++++++
Elapsed time:  0.028260501000659133
Stopped at epoch:  0
1/1 [==============================] - 0s 16ms/step
+++++++++++ [1_5] | 11 ++++++++++++++++++
Elapsed time:  0.03891294999993988
Stopped at epoch:  0
1/1 [==============================] - 0s 18ms/step
+++++++++++ [1_5] | 12 ++++++++++++++++++
Elapsed t

r2   r2_test    r2_val     r2_vt       mse  mse_test  \
model_2_1_0   0.733239  0.171449  0.365200  0.301359  0.295225  0.593895   
model_2_1_22  0.771427  0.846326  0.166072  0.393627  0.252963  0.110152   
model_2_1_21  0.771791  0.845809  0.168107  0.394809  0.252561  0.110522   
model_2_1_20  0.771840  0.845341  0.169336  0.395470  0.252505  0.110858   
model_2_1_19  0.772403  0.847720  0.171307  0.397577  0.251883  0.109152   
model_2_1_17  0.772536  0.847536  0.173050  0.398676  0.251735  0.109284   
model_2_1_18  0.774846  0.850669  0.182101  0.405744  0.249180  0.107039   
model_2_1_16  0.775588  0.846148  0.188766  0.408678  0.248358  0.110279   
model_2_1_3   0.777800  0.851087  0.207809  0.423000  0.245910  0.106739   
model_2_1_6   0.777929  0.854535  0.202005  0.420284  0.245767  0.104267   
model_2_1_5   0.778184  0.853422  0.204168  0.421353  0.245485  0.105065   
model_2_1_9   0.778268  0.848101  0.203359  0.419040  0.245392  0.108879   
model_2_1_7   0.778361  0.858575  0.200634  0.420717  0.245289  0.101371   
model_2_1_10  0.778918  0.849793  0.205125  0.420780  0.244673  0.107666   
model_2_1_4   0.779843  0.856536  0.211607  0.427343  0.243649  0.102833   
model_2_1_13  0.779875  0.850571  0.208794  0.423483  0.243614  0.107109   
model_2_1_12  0.780390  0.849575  0.211843  0.425181  0.243044  0.107823   
model_2_1_8   0.780424  0.847295  0.214205  0.425992  0.243006  0.109457   
model_2_1_14  0.780758  0.848728  0.213426  0.425952  0.242636  0.108430   
model_2_1_15  0.780906  0.850684  0.213096  0.426385  0.242473  0.107028   
model_2_1_11  0.781677  0.853525  0.216210  0.429403  0.241620  0.104991   
model_2_1_2   0.787490  0.870990  0.246733  0.455543  0.235186  0.092473   
model_2_1_1   0.795256  0.864353  0.292444  0.483763  0.226591  0.097230   

               mse_val    mse_vt  
model_2_1_0   1.022928  0.795794  
model_2_1_22  1.343808  0.690696  
model_2_1_21  1.340528  0.689349  
model_2_1_20  1.338548  0.688596  
model_2_1_19  1.335372  0.686196  
model_2_1_17  1.332562  0.684945  
model_2_1_18  1.317978  0.676893  
model_2_1_16  1.307237  0.673552  
model_2_1_3   1.276552  0.657238  
model_2_1_6   1.285904  0.660332  
model_2_1_5   1.282419  0.659114  
model_2_1_9   1.283723  0.661749  
model_2_1_7   1.288113  0.659839  
model_2_1_10  1.280876  0.659766  
model_2_1_4   1.270432  0.652290  
model_2_1_13  1.274963  0.656687  
model_2_1_12  1.270051  0.654754  
model_2_1_8   1.266246  0.653829  
model_2_1_14  1.267499  0.653875  
model_2_1_15  1.268032  0.653382  
model_2_1_11  1.263014  0.649944  
model_2_1_2   1.213828  0.620169  
model_2_1_1   1.140170  0.588025

...

DataFrame salvo em ../results/metrics_28_7
+++++++++++ [28_8] | 1 ++++++++++++++++++
Elapsed time:  0.03194804400118301
Stopped at epoch:  0
1/1 [==============================] - 0s 15ms/step
+++++++++++ [28_8] | 2 ++++++++++++++++++
Elapsed time:  0.026622002000294742
Stopped at epoch:  0
1/1 [==============================] - 0s 17ms/step
+++++++++++ [28_8] | 3 ++++++++++++++++++
Elapsed time:  0.025825783999607665
Stopped at epoch:  0
1/1 [==============================] - 0s 16ms/step
+++++++++++ [28_8] | 4 ++++++++++++++++++
Elapsed time:  0.024051758000496193
Stopped at epoch:  0
1/1 [==============================] - 0s 16ms/step
+++++++++++ [28_8] | 5 ++++++++++++++++++
Elapsed time:  0.031977968999854056
Stopped at epoch:  0
1/1 [==============================] - 0s 17ms/step
+++++++++++ [28_8] | 6 ++++++++++++++++++
Elapsed time:  0.030425705001107417
Stopped at epoch:  0
1/1 [==============================] - 0s 24ms/step
+++++++++++ [28_8] | 7 ++++++++++++++++++
Elapsed ti

r2   r2_test    r2_val     r2_vt       mse  mse_test  \
model_28_8_0   0.837846  0.859706  0.834203  0.868547  0.179457  0.228053   
model_28_8_22  0.837846  0.859706  0.834203  0.868547  0.179457  0.228053   
model_28_8_21  0.837846  0.859706  0.834203  0.868547  0.179457  0.228053   
model_28_8_20  0.837846  0.859706  0.834203  0.868547  0.179457  0.228053   
model_28_8_19  0.837846  0.859706  0.834203  0.868547  0.179457  0.228053   
model_28_8_18  0.837846  0.859706  0.834203  0.868547  0.179457  0.228053   
model_28_8_17  0.837846  0.859706  0.834203  0.868547  0.179457  0.228053   
model_28_8_16  0.837846  0.859706  0.834203  0.868547  0.179457  0.228053   
model_28_8_15  0.837846  0.859706  0.834203  0.868547  0.179457  0.228053   
model_28_8_14  0.837846  0.859706  0.834203  0.868547  0.179457  0.228053   
model_28_8_13  0.837846  0.859706  0.834203  0.868547  0.179457  0.228053   
model_28_8_23  0.837846  0.859706  0.834203  0.868547  0.179457  0.228053   
model_28_8_12  0.837846  0.859706  0.834203  0.868547  0.179457  0.228053   
model_28_8_10  0.837846  0.859706  0.834203  0.868547  0.179457  0.228053   
model_28_8_9   0.837846  0.859706  0.834203  0.868547  0.179457  0.228053   
model_28_8_8   0.837846  0.859706  0.834203  0.868547  0.179457  0.228053   
model_28_8_7   0.837846  0.859706  0.834203  0.868547  0.179457  0.228053   
model_28_8_6   0.837846  0.859706  0.834203  0.868547  0.179457  0.228053   
model_28_8_5   0.837846  0.859706  0.834203  0.868547  0.179457  0.228053   
model_28_8_4   0.837846  0.859706  0.834203  0.868547  0.179457  0.228053   
model_28_8_3   0.837846  0.859706  0.834203  0.868547  0.179457  0.228053   
model_28_8_2   0.837846  0.859706  0.834203  0.868547  0.179457  0.228053   
model_28_8_1   0.837846  0.859706  0.834203  0.868547  0.179457  0.228053   
model_28_8_11  0.837846  0.859706  0.834203  0.868547  0.179457  0.228053   
model_28_8_24  0.837846  0.859706  0.834203  0.868547  0.179457  0.228053   

                mse_val   mse_vt  
model_28_8_0   0.316532  0.26969  
model_28_8_22  0.316532  0.26969  
model_28_8_21  0.316532  0.26969  
model_28_8_20  0.316532  0.26969  
model_28_8_19  0.316532  0.26969  
model_28_8_18  0.316532  0.26969  
model_28_8_17  0.316532  0.26969  
model_28_8_16  0.316532  0.26969  
model_28_8_15  0.316532  0.26969  
model_28_8_14  0.316532  0.26969  
model_28_8_13  0.316532  0.26969  
model_28_8_23  0.316532  0.26969  
model_28_8_12  0.316532  0.26969  
model_28_8_10  0.316532  0.26969  
model_28_8_9   0.316532  0.26969  
model_28_8_8   0.316532  0.26969  
model_28_8_7   0.316532  0.26969  
model_28_8_6   0.316532  0.26969  
model_28_8_5   0.316532  0.26969  
model_28_8_4   0.316532  0.26969  
model_28_8_3   0.316532  0.26969  
model_28_8_2   0.316532  0.26969  
model_28_8_1   0.316532  0.26969  
model_28_8_11  0.316532  0.26969  
model_28_8_24  0.316532  0.26969

DataFrame salvo em ../results/metrics_28_8
+++++++++++ [28_9] | 1 ++++++++++++++++++
Elapsed time:  0.035562758001105976
Stopped at epoch:  0
1/1 [==============================] - 0s 17ms/step
+++++++++++ [28_9] | 2 ++++++++++++++++++
Elapsed time:  0.02719139699911466
Stopped at epoch:  0
1/1 [==============================] - 0s 17ms/step
+++++++++++ [28_9] | 3 ++++++++++++++++++
Elapsed time:  0.02439621499979694
Stopped at epoch:  0
1/1 [==============================] - 0s 16ms/step
+++++++++++ [28_9] | 4 ++++++++++++++++++
Elapsed time:  0.02592283400008455
Stopped at epoch:  0
1/1 [==============================] - 0s 22ms/step
+++++++++++ [28_9] | 5 ++++++++++++++++++
Elapsed time:  0.02813156299998809
Stopped at epoch:  0
1/1 [==============================] - 0s 19ms/step
+++++++++++ [28_9] | 6 ++++++++++++++++++
Elapsed time:  0.028796389000490308
Stopped at epoch:  0
1/1 [==============================] - 0s 17ms/step
+++++++++++ [28_9] | 7 ++++++++++++++++++
Elapsed time:

r2  r2_test    r2_val     r2_vt       mse  mse_test  \
model_28_9_0   0.837846  0.76726  0.929953  0.802641  0.179457  0.207953   
model_28_9_22  0.837846  0.76726  0.929953  0.802641  0.179457  0.207953   
model_28_9_21  0.837846  0.76726  0.929953  0.802641  0.179457  0.207953   
model_28_9_20  0.837846  0.76726  0.929953  0.802641  0.179457  0.207953   
model_28_9_19  0.837846  0.76726  0.929953  0.802641  0.179457  0.207953   
model_28_9_18  0.837846  0.76726  0.929953  0.802641  0.179457  0.207953   
model_28_9_17  0.837846  0.76726  0.929953  0.802641  0.179457  0.207953   
model_28_9_16  0.837846  0.76726  0.929953  0.802641  0.179457  0.207953   
model_28_9_15  0.837846  0.76726  0.929953  0.802641  0.179457  0.207953   
model_28_9_14  0.837846  0.76726  0.929953  0.802641  0.179457  0.207953   
model_28_9_13  0.837846  0.76726  0.929953  0.802641  0.179457  0.207953   
model_28_9_23  0.837846  0.76726  0.929953  0.802641  0.179457  0.207953   
model_28_9_12  0.837846  0.76726  0.929953  0.802641  0.179457  0.207953   
model_28_9_10  0.837846  0.76726  0.929953  0.802641  0.179457  0.207953   
model_28_9_9   0.837846  0.76726  0.929953  0.802641  0.179457  0.207953   
model_28_9_8   0.837846  0.76726  0.929953  0.802641  0.179457  0.207953   
model_28_9_7   0.837846  0.76726  0.929953  0.802641  0.179457  0.207953   
model_28_9_6   0.837846  0.76726  0.929953  0.802641  0.179457  0.207953   
model_28_9_5   0.837846  0.76726  0.929953  0.802641  0.179457  0.207953   
model_28_9_4   0.837846  0.76726  0.929953  0.802641  0.179457  0.207953   
model_28_9_3   0.837846  0.76726  0.929953  0.802641  0.179457  0.207953   
model_28_9_2   0.837846  0.76726  0.929953  0.802641  0.179457  0.207953   
model_28_9_1   0.837846  0.76726  0.929953  0.802641  0.179457  0.207953   
model_28_9_11  0.837846  0.76726  0.929953  0.802641  0.179457  0.207953   
model_28_9_24  0.837846  0.76726  0.929953  0.802641  0.179457  0.207953   

                mse_val    mse_vt  
model_28_9_0   0.006521  0.113161  
model_28_9_22  0.006521  0.113161  
model_28_9_21  0.006521  0.113161  
model_28_9_20  0.006521  0.113161  
model_28_9_19  0.006521  0.113161  
model_28_9_18  0.006521  0.113161  
model_28_9_17  0.006521  0.113161  
model_28_9_16  0.006521  0.113161  
model_28_9_15  0.006521  0.113161  
model_28_9_14  0.006521  0.113161  
model_28_9_13  0.006521  0.113161  
model_28_9_23  0.006521  0.113161  
model_28_9_12  0.006521  0.113161  
model_28_9_10  0.006521  0.113161  
model_28_9_9   0.006521  0.113161  
model_28_9_8   0.006521  0.113161  
model_28_9_7   0.006521  0.113161  
model_28_9_6   0.006521  0.113161  
model_28_9_5   0.006521  0.113161  
model_28_9_4   0.006521  0.113161  
model_28_9_3   0.006521  0.113161  
model_28_9_2   0.006521  0.113161  
model_28_9_1   0.006521  0.113161  
model_28_9_11  0.006521  0.113161  
model_28_9_24  0.006521  0.113161

DataFrame salvo em ../results/metrics_28_9
